In this notebook, I will test the hypothesis that long a basket of BDC (Business Development / Specialty Lending Companies) can decrease the volatility and increase the returns of a long market portfolio. I came up with this idea after finding that this basket of BDC companies (dividend-adjusted) outperforms market returns yet has between a -2.5 to -3.1 Mkt-Rf parameter after running a historical Fama-French Macbeth regression (post-covid to present, Nov 2023).

If this is true, it could substitute the traditional 60/40 portfolio and allow investors to increase their portfolio's sharpe without requiring any increase in 'activeness' of management or time spent on researching good debt.

In [128]:
# imports
import pandas as pd
import numpy as np
import yfinance as yf
import plotly.graph_objects as go

In [129]:
# Basket of BDC tickers
bdc_tickers = ['ARCC', 'BBDC', 'BCSF', 'BKCC', 'BXSL', 'CCAP', 'CGBD', 'CION', 'CSWC', 'FCRD', 'FDUS', 'FSK', 'GAIN', 'GBDC', 'GECC', 'GLAD', 'GSBD', 'HRZN', 'HTGC', 'ICMB', 'LRFC', 'MAIN', 'MFIC', 'MRCC', 'NMFC', 'OBDC', 'OCSL', 'OFS', 'OXSQ', 'PFLT']

In [130]:
start = '2010-01-01'
end = '2023-11-01'

mkt = yf.Ticker('SPY').history(start=start, end=end, interval='1d')
mkt['Div Adj Close'] = mkt['Close'].copy()
dividends = mkt['Dividends'].copy()
for date, div in dividends.items():
    if div > 0:
        mkt.loc[date:, 'Div Adj Close'] *= (1 + div / mkt.loc[date, 'Close'])

mkt.head()

Open       High        Low      Close  \
Date                                                                    
2010-01-04 00:00:00-05:00  86.742152  87.529522  86.078289  87.483208   
2010-01-05 00:00:00-05:00  87.429164  87.753374  87.112668  87.714775   
2010-01-06 00:00:00-05:00  87.629843  87.992652  87.560372  87.776512   
2010-01-07 00:00:00-05:00  87.614413  88.255119  87.367395  88.147049   
2010-01-08 00:00:00-05:00  87.915484  88.478998  87.737943  88.440399   

                              Volume  Dividends  Stock Splits  Capital Gains  \
Date                                                                           
2010-01-04 00:00:00-05:00  118944600        0.0           0.0            0.0   
2010-01-05 00:00:00-05:00  111579900        0.0           0.0            0.0   
2010-01-06 00:00:00-05:00  116074400        0.0           0.0            0.0   
2010-01-07 00:00:00-05:00  131091100        0.0           0.0            0.0   
2010-01-08 00:00:00-05:00  126402800        0.0           0.0            0.0   

                           Div Adj Close  
Date                                      
2010-01-04 00:00:00-05:00      87.483208  
2010-01-05 00:00:00-05:00      87.714775  
2010-01-06 00:00:00-05:00      87.776512  
2010-01-07 00:00:00-05:00      88.147049  
2010-01-08 00:00:00-05:00      88.440399

In [131]:
# Plot market returns
fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt.index, y=mkt['Div Adj Close'], name='Div Adj'))
fig.add_trace(go.Scatter(x=mkt.index, y=mkt['Close'], name='SPY'))
fig.update_layout(title='Market Returns', xaxis_title='Date', yaxis_title='Price')
fig.show()

In [132]:
# We will use Oaktree Specialty Lending (OCSL) as an example for preliminary analysis

ocsl = yf.Ticker('OCSL').history(start=start, end=end, interval='1d')
ocsl['Div Adj Close'] = ocsl['Close'].copy()
dividends = ocsl['Dividends'].copy()
for date, div in dividends.items():
    if div > 0:
        ocsl.loc[date:, 'Div Adj Close'] *= (1 + div / ocsl.loc[date, 'Close'])

ocsl.head()

Open      High       Low     Close  Volume  \
Date                                                                        
2010-01-04 00:00:00-05:00  8.359824  8.589070  8.329258  8.474447  104500   
2010-01-05 00:00:00-05:00  8.436234  8.573781  8.428593  8.527932   82933   
2010-01-06 00:00:00-05:00  8.474446  8.657842  8.451521  8.604351   60400   
2010-01-07 00:00:00-05:00  8.619637  8.665486  8.459164  8.596712   52100   
2010-01-08 00:00:00-05:00  8.680769  8.986429  8.680769  8.986429   79533   

                           Dividends  Stock Splits  Div Adj Close  
Date                                                               
2010-01-04 00:00:00-05:00        0.0           0.0       8.474447  
2010-01-05 00:00:00-05:00        0.0           0.0       8.527932  
2010-01-06 00:00:00-05:00        0.0           0.0       8.604351  
2010-01-07 00:00:00-05:00        0.0           0.0       8.596712  
2010-01-08 00:00:00-05:00        0.0           0.0       8.986429

In [133]:
# Plot OCSL returns
fig = go.Figure()
fig.add_trace(go.Scatter(x=ocsl.index, y=ocsl['Div Adj Close'], name='Div Adj'))
fig.add_trace(go.Scatter(x=ocsl.index, y=ocsl['Close'], name='OCSL'))
fig.update_layout(title='OCSL Returns', xaxis_title='Date', yaxis_title='Price')
fig.show()

In [134]:
# Construction of the market and OCSL portfolios
mkt['Returns'] = mkt['Div Adj Close'].pct_change()
ocsl['Returns'] = ocsl['Div Adj Close'].pct_change()

In [135]:
mkt['Cumulative Returns'] = (1 + mkt['Returns']).cumprod()
ocsl['Cumulative Returns'] = (1 + ocsl['Returns']).cumprod()

In [136]:
# Plot cumulative returns
fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt.index, y=mkt['Cumulative Returns'], name='SPY'))
fig.add_trace(go.Scatter(x=ocsl.index, y=ocsl['Cumulative Returns'], name='OCSL'))
fig.update_layout(title='Cumulative Returns', xaxis_title='Date', yaxis_title='Price')
fig.show()

In [137]:
# Plot Returns Distribution
fig = go.Figure()
fig.add_trace(go.Histogram(x=mkt['Returns'], name='SPY'))
fig.update_layout(title='Market Returns Distribution', xaxis_title='Returns', yaxis_title='Frequency')
fig.show()

fig2 = go.Figure()
fig2.add_trace(go.Histogram(x=ocsl['Returns'], name='OCSL'))
fig2.update_layout(title='OCSL Returns Distribution', xaxis_title='Returns', yaxis_title='Frequency')
fig2.show()

In [138]:
mkt_vol = mkt['Returns'].std() * np.sqrt(252)
ocsl_vol = ocsl['Returns'].std() * np.sqrt(252)

print('Market Volatility: {:.2f}%'.format(mkt_vol * 100))
print('OCSL Volatility: {:.2f}%'.format(ocsl_vol * 100))

Market Volatility: 17.38%
OCSL Volatility: 27.94%


# Combined Portfolio

In [139]:
# 25% OCSL, 75% SPY Portfolio

ocsl_wt = 0.25
mkt_wt = 1 - ocsl_wt

quarter_pf = ocsl_wt * ocsl['Returns'] + mkt_wt * mkt['Returns']
quarter_pf = quarter_pf.dropna()

# 50% OCSL, 50% SPY Portfolio

ocsl_wt = 0.50
mkt_wt = 1 - ocsl_wt

half_pf = ocsl_wt * ocsl['Returns'] + mkt_wt * mkt['Returns']

# 40% OCSL, 60% SPY Portfolio

ocsl_wt = 0.40
mkt_wt = 1 - ocsl_wt

forty_pf = ocsl_wt * ocsl['Returns'] + mkt_wt * mkt['Returns']

In [140]:
# Plot Cumulative Returns
fig = go.Figure()
fig.add_trace(go.Scatter(x=quarter_pf.index, y=(1 + quarter_pf).cumprod(), name='1/4 OCSL, 3/4 SPY'))
fig.add_trace(go.Scatter(x=half_pf.index, y=(1 + half_pf).cumprod(), name='1/2 OCSL, 1/2 SPY'))
fig.add_trace(go.Scatter(x=forty_pf.index, y=(1 + forty_pf).cumprod(), name='2/5 OCSL, 3/5 SPY'))
fig.add_trace(go.Scatter(x=mkt.index, y=mkt['Cumulative Returns'], name='SPY'))
fig.update_layout(title='Cumulative Returns', xaxis_title='Date', yaxis_title='Price')
fig.show()

In [141]:
# Create monthly returns portfolios

mkt_monthly = mkt['Div Adj Close'].resample('M').last()
mkt_monthly = mkt_monthly.pct_change().dropna()

ocsl_monthly = ocsl['Div Adj Close'].resample('M').last()
ocsl_monthly = ocsl_monthly.pct_change().dropna()

# 25% OCSL, 75% SPY Portfolio

ocsl_wt = 0.25
mkt_wt = 1 - ocsl_wt

quarter_pf_monthly = ocsl_wt * ocsl_monthly + mkt_wt * mkt_monthly
quarter_pf_monthly = quarter_pf_monthly.dropna()

# 50% OCSL, 50% SPY Portfolio

ocsl_wt = 0.50
mkt_wt = 1 - ocsl_wt

half_pf_monthly = ocsl_wt * ocsl_monthly + mkt_wt * mkt_monthly

# 40% OCSL, 60% SPY Portfolio

ocsl_wt = 0.40

mkt_wt = 1 - ocsl_wt

forty_pf_monthly = ocsl_wt * ocsl_monthly + mkt_wt * mkt_monthly

In [142]:
# Compare the variance of the portfolios

quarter_vol = quarter_pf.std() * np.sqrt(252)
half_vol = half_pf.std() * np.sqrt(252)
forty_vol = forty_pf.std() * np.sqrt(252)

print('1/4 OCSL Volatility: {:.2f}%'.format(quarter_vol * 100))
print('1/2 OCSL Volatility: {:.2f}%'.format(half_vol * 100))
print('60/40 Mkt:OCSL Volatility: {:.2f}%'.format(forty_vol * 100))
print('Market Volatility: {:.2f}%'.format(mkt_vol * 100))

1/4 OCSL Volatility: 17.54%
1/2 OCSL Volatility: 19.73%
60/40 Mkt:OCSL Volatility: 18.64%
Market Volatility: 17.38%


In [143]:
# Compare Sharpe Ratios

rfr = 0.02

quarter_sharpe = ((quarter_pf.mean() * 252) - rfr) / quarter_vol
half_sharpe = ((half_pf.mean() * 252) - rfr) / half_vol
forty_sharpe = ((forty_pf.mean() * 252) - rfr) / forty_vol
mkt_sharpe = ((mkt['Returns'].mean() * 252) - rfr) / mkt_vol

print('1/4 OCSL Sharpe Ratio: {:.2f}'.format(quarter_sharpe))
print('1/2 OCSL Sharpe Ratio: {:.2f}'.format(half_sharpe))
print('60/40 Mkt:OCSL Sharpe Ratio: {:.2f}'.format(forty_sharpe))
print('Market Sharpe Ratio: {:.2f}'.format(mkt_sharpe))

1/4 OCSL Sharpe Ratio: 0.96
1/2 OCSL Sharpe Ratio: 1.06
60/40 Mkt:OCSL Sharpe Ratio: 1.03
Market Sharpe Ratio: 0.75


In [144]:
# Plot the market daily returns on the x axis and the OCSL daily returns on the y axis

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt['Returns'], y=ocsl['Returns'], mode='markers'))
fig.update_layout(title='Market v OCSL Daily Returns', xaxis_title='SPY', yaxis_title='OCSL')
fig.show()

In [151]:
# Drop the first row in mkt
mkt = mkt.iloc[1:]

In [157]:
mkt['Cumulative Returns']

Date
2010-01-05 00:00:00-05:00    1.002647
2010-01-06 00:00:00-05:00    1.003353
2010-01-07 00:00:00-05:00    1.007588
2010-01-08 00:00:00-05:00    1.010941
2010-01-11 00:00:00-05:00    1.012353
                               ...   
2023-10-25 00:00:00-04:00    6.413712
2023-10-26 00:00:00-04:00    6.336910
2023-10-27 00:00:00-04:00    6.308186
2023-10-30 00:00:00-04:00    6.383606
2023-10-31 00:00:00-04:00    6.423696
Name: Cumulative Returns, Length: 3480, dtype: float64

In [172]:
cum_ret_df = pd.DataFrame(mkt['Cumulative Returns'])
cum_ret_df.rename(columns={'Cumulative Returns': 'SPY'}, inplace=True)
cum_ret_df.index = pd.to_datetime(cum_ret_df.index).tz_localize(None)
forty_pf_cum_ret = (1 + forty_pf).cumprod()
cum_ret_df['60/40 Mkt/OCSL'] = list(forty_pf_cum_ret)[1:]
cum_ret_df.to_excel('cum_ret_df.xlsx')

In [160]:
# Plot the market portfolio vs the 60/40 portfolio

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt.index, y=mkt['Cumulative Returns'], name='SPY'))
fig.add_trace(go.Scatter(x=forty_pf.index, y=(1 + forty_pf).cumprod(), name='60/40 Mkt:OCSL'))
fig.update_layout(title='Cumulative Returns', xaxis_title='Date', yaxis_title='Price')
fig.show()

Date  SPY
0 2010-01-05  NaN
1 2010-01-06  NaN
2 2010-01-07  NaN
3 2010-01-08  NaN
4 2010-01-11  NaN

In [193]:
rolling_vol_df = pd.DataFrame()
rolling_vol_df['Date'] = mkt.index.tz_localize(None)
spy_vol= list(mkt['Returns'].rolling(252).std() * np.sqrt(252))
forty_pf_vol = list(forty_pf.rolling(252).std() * np.sqrt(252))[1:]
rolling_vol_df['SPY'] = spy_vol
rolling_vol_df['60/40 Mkt/OCSL'] = forty_pf_vol
rolling_vol_df = rolling_vol_df.dropna()
rolling_vol_df.to_excel('rolling_vol_df.xlsx')

In [173]:
# Plot the market portfolio variance vs the 60/40 portfolio variance

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt.index, y=mkt['Returns'].rolling(252).std() * np.sqrt(252), name='SPY'))
fig.add_trace(go.Scatter(x=forty_pf.index, y=forty_pf.rolling(252).std() * np.sqrt(252), name='60/40 Mkt:OCSL'))
fig.update_layout(title='Rolling Volatility', xaxis_title='Date', yaxis_title='Volatility')
fig.show()

# Export rolling volatility to an excel
rolling_volatility = pd.DataFrame()
# remove timezones
rolling_volatility['Date'] = mkt.index.tz_localize(None)
rolling_volatility['SPY'] = mkt['Returns'].rolling(252).std() * np.sqrt(252)
# rolling_volatility['60/40 Mkt:OCSL'] = forty_pf.rolling(252).std() * np.sqrt(252)
# rolling_volatility.to_excel('rolling_volatility.xlsx', index=False)

Date  SPY
0 2010-01-05  NaN
1 2010-01-06  NaN
2 2010-01-07  NaN
3 2010-01-08  NaN
4 2010-01-11  NaN

In [195]:
rolling_sharpe_df = pd.DataFrame()
rolling_sharpe_df['Date'] = mkt.index.tz_localize(None)
spy_sharpe = list((mkt['Returns'].rolling(252).mean() * 252 - 0.02) / (mkt['Returns'].rolling(252).std() * np.sqrt(252)))
forty_pf_sharpe = list((forty_pf.rolling(252).mean() * 252 - 0.02) / (forty_pf.rolling(252).std() * np.sqrt(252)))[1:]
rolling_sharpe_df['SPY'] = spy_sharpe
rolling_sharpe_df['60/40 Mkt/OCSL'] = forty_pf_sharpe
rolling_sharpe_df = rolling_sharpe_df.dropna()
rolling_sharpe_df.to_excel('rolling_sharpe_df.xlsx')

In [147]:
# Plot the rolling sharpe ratios

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt.index, y=((mkt['Returns'].rolling(252).mean() * 252) - rfr) / (mkt['Returns'].rolling(252).std() * np.sqrt(252)), name='SPY'))
fig.add_trace(go.Scatter(x=forty_pf.index, y=((forty_pf.rolling(252).mean() * 252) - rfr) / (forty_pf.rolling(252).std() * np.sqrt(252)), name='60/40 Mkt:OCSL'))
fig.update_layout(title='Rolling Sharpe Ratio', xaxis_title='Date', yaxis_title='Sharpe Ratio')
fig.show()

# Export rolling sharpe ratios to an excel
rolling_sharpe = pd.DataFrame()
# remove timezones
rolling_sharpe['Date'] = mkt.index.tz_localize(None)
rolling_sharpe['SPY'] = ((mkt['Returns'].rolling(252).mean() * 252) - rfr) / (mkt['Returns'].rolling(252).std() * np.sqrt(252))
rolling_sharpe['60/40 Mkt:OCSL'] = ((forty_pf.rolling(252).mean() * 252) - rfr) / (forty_pf.rolling(252).std() * np.sqrt(252))
rolling_sharpe.to_excel('rolling_sharpe.xlsx', index=False)

# Now, with the basket of BDC companies

In [107]:
# Create a dictionary to store the historical data for each stock
stock_data_dict = {}

# Fetch historical data for each stock
for ticker in bdc_tickers:
    try:
        tic = yf.Ticker(ticker)
        stock_data = tic.history(start=start, end=end, interval="1wk")  # Weekly data
        dividends = stock_data['Dividends']
        stock_data['Adj Close with Div'] = stock_data['Close'].copy()
        for date, div in dividends.items():
            if div > 0:
                stock_data.loc[date:, 'Adj Close with Div'] *= (1 + div / stock_data.loc[date, 'Close'])
        stock_data_dict[ticker] = stock_data
    except Exception as e:
        print(f"Error fetching data for {ticker}: {e}")

sample_ticker = bdc_tickers[0]
print(stock_data_dict[sample_ticker].head())

                               Open      High       Low     Close    Volume  \
Date                                                                          
2010-01-01 00:00:00-05:00  3.443690  3.671282  3.400339  3.600837   5581600   
2010-01-08 00:00:00-05:00  3.603547  3.755275  3.535811  3.733600   5755300   
2010-01-15 00:00:00-05:00  3.752565  3.879909  3.584580  3.663154   8062200   
2010-01-22 00:00:00-05:00  3.663154  3.676701  3.400338  3.411176  25852800   
2010-01-29 00:00:00-05:00  3.435561  3.454527  3.183583  3.183583  11092500   

                           Dividends  Stock Splits  Adj Close with Div  
Date                                                                    
2010-01-01 00:00:00-05:00        0.0           0.0            3.600837  
2010-01-08 00:00:00-05:00        0.0           0.0            3.733600  
2010-01-15 00:00:00-05:00        0.0           0.0            3.663154  
2010-01-22 00:00:00-05:00        0.0           0.0            3.411176  
2010-01-

In [108]:
# We can condense all these dataframes into a single one with the same date range and the assets as columns

# Create a new dataframe to store the adjusted close price of the stocks
adj_close_df = pd.DataFrame(index=stock_data_dict[sample_ticker].index)

# Add the adjusted close price of each stock to the dataframe
for ticker in stock_data_dict.keys():
    adj_close_df[ticker] = stock_data_dict[ticker]['Adj Close with Div']

# Remove columns with more than 5% missing values
adj_close_df = adj_close_df.dropna(axis=1, thresh=int(len(adj_close_df) * 0.95))

adj_close_df.head()

ARCC      BBDC      BKCC      CSWC      GAIN  \
Date                                                                          
2010-01-01 00:00:00-05:00  3.600837  3.111938  2.022560  2.674881  1.399755   
2010-01-08 00:00:00-05:00  3.733600  3.124672  2.048429  2.715698  1.419794   
2010-01-15 00:00:00-05:00  3.663154  3.101753  2.053133  2.695619  1.399680   
2010-01-22 00:00:00-05:00  3.411176  3.055914  2.109576  2.699240  1.414292   
2010-01-29 00:00:00-05:00  3.183583  3.015169  2.090762  2.659738  1.369724   

                               GLAD      HTGC      MAIN      MFIC      OCSL  \
Date                                                                          
2010-01-01 00:00:00-05:00  2.165630  2.769894  5.486311  6.743716  8.596709   
2010-01-08 00:00:00-05:00  2.182289  2.782706  5.082176  7.063953  8.894729   
2010-01-15 00:00:00-05:00  2.182877  2.741708  5.113810  6.963486  8.971147   
2010-01-22 00:00:00-05:00  2.081275  2.626403  5.136236  6.486276  8.428594   
2010-01-29 00:00:00-05:00  2.234693  2.498286  5.011746  6.235114  8.130580   

                               OXSQ  
Date                                 
2010-01-01 00:00:00-05:00  0.971999  
2010-01-08 00:00:00-05:00  0.991026  
2010-01-15 00:00:00-05:00  0.979927  
2010-01-22 00:00:00-05:00  0.932358  
2010-01-29 00:00:00-05:00  0.926015

In [114]:
returns = adj_close_df.pct_change().dropna()
bdc_returns= returns.mean(axis=1)
bdc_returns.head()

Date
2010-01-08 00:00:00-05:00    0.011247
2010-01-15 00:00:00-05:00   -0.006412
2010-01-22 00:00:00-05:00   -0.027824
2010-01-29 00:00:00-05:00   -0.019573
2010-02-05 00:00:00-05:00    0.034807
dtype: float64

In [113]:
mkt = yf.Ticker('SPY').history(start=start, end=end, interval='1wk')
mkt['Div Adj Close'] = mkt['Close'].copy()
dividends = mkt['Dividends'].copy()
for date, div in dividends.items():
    if div > 0:
        mkt.loc[date:, 'Div Adj Close'] *= (1 + div / mkt.loc[date, 'Close'])

mkt_returns = mkt['Div Adj Close'].pct_change().dropna()
mkt_returns = mkt_returns.resample('W').last()
mkt_returns.head()

Date
2010-01-10 00:00:00-05:00    0.006480
2010-01-17 00:00:00-05:00   -0.028104
2010-01-24 00:00:00-05:00   -0.028021
2010-01-31 00:00:00-05:00   -0.019619
2010-02-07 00:00:00-05:00    0.015877
Freq: W-SUN, Name: Div Adj Close, dtype: float64

In [115]:
# Plot the market returns on x axis and the BDC returns on the y axis

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt_returns, y=bdc_returns, mode='markers'))
fig.update_layout(title='Market v BDC Weekly Returns', xaxis_title='SPY', yaxis_title='BDC')
fig.show()

In [116]:
# Plot cumulative returns

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt_returns.index, y=(1 + mkt_returns).cumprod(), name='SPY'))
fig.add_trace(go.Scatter(x=bdc_returns.index, y=(1 + bdc_returns).cumprod(), name='BDC'))
fig.update_layout(title='Cumulative Returns', xaxis_title='Date', yaxis_title='Price')
fig.show()

In [122]:
# export the cumulative returns data to an excel file
cumulative_returns = pd.DataFrame()
# convert mkt and bdc returns to datetimes without timezones
mkt_returns.index = pd.to_datetime(mkt_returns.index).tz_localize(None)
bdc_returns.index = pd.to_datetime(bdc_returns.index).tz_localize(None)
cumulative_returns['SPY'] = (1 + mkt_returns).cumprod()
cumulative_returns['BDC'] = (1 + bdc_returns).cumprod()
cumulative_returns.to_excel('cumulative_returns.xlsx')

In [117]:
# Plot rolling volatility

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt_returns.index, y=mkt_returns.rolling(52).std() * np.sqrt(52), name='SPY'))
fig.add_trace(go.Scatter(x=bdc_returns.index, y=bdc_returns.rolling(52).std() * np.sqrt(52), name='BDC'))
fig.update_layout(title='Rolling Volatility', xaxis_title='Date', yaxis_title='Volatility')
fig.show()

In [123]:
# Convert the rolling volatility to an excel
rolling_vol = pd.DataFrame()
rolling_vol['SPY'] = mkt_returns.rolling(52).std() * np.sqrt(52)
rolling_vol['BDC'] = bdc_returns.rolling(52).std() * np.sqrt(52)
rolling_vol.to_excel('rolling_vol.xlsx')

In [118]:
# Plot rolling sharpes

fig = go.Figure()
fig.add_trace(go.Scatter(x=mkt_returns.index, y=((mkt_returns.rolling(52).mean() * 52) - rfr) / (mkt_returns.rolling(52).std() * np.sqrt(52)), name='SPY'))
fig.add_trace(go.Scatter(x=bdc_returns.index, y=((bdc_returns.rolling(52).mean() * 52) - rfr) / (bdc_returns.rolling(52).std() * np.sqrt(52)), name='BDC'))
fig.update_layout(title='Rolling Sharpe Ratio', xaxis_title='Date', yaxis_title='Sharpe Ratio')
fig.show()

In [124]:
# Convert the rolling sharpes to an excel
rolling_sharpe = pd.DataFrame()
rolling_sharpe['SPY'] = ((mkt_returns.rolling(52).mean() * 52) - rfr) / (mkt_returns.rolling(52).std() * np.sqrt(52))
rolling_sharpe['BDC'] = ((bdc_returns.rolling(52).mean() * 52) - rfr) / (bdc_returns.rolling(52).std() * np.sqrt(52))
rolling_sharpe.to_excel('rolling_sharpe.xlsx')

In [119]:
bdc_vol = bdc_returns.std() * np.sqrt(52)
print('BDC Volatility: {:.2f}%'.format(bdc_vol * 100))
print('Market Volatility: {:.2f}%'.format(mkt_returns.std() * np.sqrt(52) * 100))

BDC Volatility: 23.27%
Market Volatility: 15.97%


In [120]:
bdc_sharpe = ((bdc_returns.mean() * 52) - rfr) / bdc_vol
print('BDC Sharpe Ratio: {:.2f}'.format(bdc_sharpe))
print('Market Sharpe Ratio: {:.2f}'.format(((mkt_returns.mean() * 52) - rfr) / (mkt_returns.std() * np.sqrt(52))))

BDC Sharpe Ratio: 1.46
Market Sharpe Ratio: 0.80
